# SIBUR entities pairs classification


This BERT model was trained on Kaggle GPU Kernel and output submission scores **~ 0.47 score** on public leaderboard

The idea was to fine-tune bert-base or bert-multilingual models for SequenceClassification Task already known for Pytorch Pretrained BERT models (using HugginFace <code>pytorch-pretrained-bert</code> library).

## Model

There are various model architectures we can implement to detect the semantically similar sentences. For example:
- Logistic regression by converting words into vectors by using bag of words, TF-IDF
- Random Forests build using NLP features
- Converting words into vectors using word embeddings and using RNN's
- Converting words into vectors using word embeddings and using CNN's
- Combing RNN's and CNN's

There are numerous number of architectures can be used. We will use the state-of-the-art model architecture **BERT.**

## BERT (Bidirectional Encoder Representations from Transformers)


Google AI released a model called BERT. If you don't know what BERT is, please go through the following links:
- [paper](https://arxiv.org/pdf/1810.04805.pdf)
- [blog](http://jalammar.github.io/illustrated-bert/)

BERT obtains new state-of-the-art results on eleven natural language processing tasks.

We will use BERT to predict the given pair of sentences are semantically similar to each other or not.



### Required installations

We will use the [repository](https://github.com/huggingface/pytorch-pretrained-BERT) which contains the implementation of BERT and pretained models. We will install it using the following command

In [1]:
!pip install pytorch-pretrained-bert==0.6.1

     |████████████████████████████████| 114 kB 884 kB/s eta 0:00:01


### Imports

In [2]:
import os
import csv
import logging
import random
import sys

import pandas as pd
import numpy as np
import torch
from torch.utils.data import (DataLoader, RandomSampler, SequentialSampler, TensorDataset)
from torch.utils.data.distributed import DistributedSampler
from tqdm import tqdm, trange

from torch.nn import CrossEntropyLoss, MSELoss
from scipy.stats import pearsonr, spearmanr
from sklearn.metrics import matthews_corrcoef, f1_score
from sklearn.model_selection import StratifiedShuffleSplit

from pytorch_pretrained_bert.file_utils import PYTORCH_PRETRAINED_BERT_CACHE
from pytorch_pretrained_bert.modeling import BertForSequenceClassification, BertConfig, WEIGHTS_NAME, CONFIG_NAME
from pytorch_pretrained_bert.tokenization import BertTokenizer
from pytorch_pretrained_bert.optimization import BertAdam, warmup_linear

Better speed can be achieved with apex installed from https://www.github.com/nvidia/apex.


In [3]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
print(device)

cuda


In [4]:
logging.basicConfig(format = '%(asctime)s - %(levelname)s - %(name)s -   %(message)s',
                    datefmt = '%m/%d/%Y %H:%M:%S',
                    level = logging.INFO)
logger = logging.getLogger(__name__)
logger.setLevel(logging.INFO)

In [5]:
train = pd.read_csv('/kaggle/input/sibur-2020-nlp-classification/train_bert.csv')
train = train.reset_index()
train.drop('index', axis=1, inplace=True)

train.head()

pair_id                           name_1             name_2  is_duplicate
0        0              vulcaflex industria              vulco             0
1        1       lc intermational logistics           national             0
2        2                              adk             mitsui             0
3        3  tara riss arya textile industry      mj industrial             0
4        4          sheikh muhammad trading  maa ganga trading             0

We can also split train dataset for evaluation using Stratified Split, but for simplicity we'll train our model on full train dataset

In [6]:
# split = StratifiedShuffleSplit(1, train_size=0.8, random_state=42)
# tridx, cvidx = list(split.split(data[['name_1', 'name_2']], data["is_duplicate"]))[0]

In [7]:
# train = data.iloc[tridx]
# eval = data.iloc[cvidx]

In [8]:
# eval.is_duplicate.value_counts()

### Input Feature Representation

Classes to represent each Example and InputFeature (example tokenization, segment ids etc..)

In [9]:
class InputExample(object):
    """A single training/test example for simple sequence classification."""

    def __init__(self, guid, text_a, text_b=None, label=None):
        """Constructs a InputExample.
        Args:
            guid: Unique id for the example.
            text_a: string. The untokenized text of the first sequence. For single
            sequence tasks, only this sequence must be specified.
            text_b: (Optional) string. The untokenized text of the second sequence.
            Only must be specified for sequence pair tasks.
            label: (Optional) string. The label of the example. This should be
            specified for train and dev examples, but not for test examples.
        """
        self.guid = guid
        self.text_a = text_a
        self.text_b = text_b
        self.label = label

        
class InputFeatures(object):
    """A single set of features of data."""

    def __init__(self, input_ids, input_mask, segment_ids, label_id):
        self.input_ids = input_ids
        self.input_mask = input_mask
        self.segment_ids = segment_ids
        self.label_id = label_id

### Data Processor

For reading the dataset and converting each sample in dataset into examples.

In [10]:
class DataPreProcessor():
    
    def get_labels(self):
        """Returns all the types of labels present in the data."""
        
        return ["0", "1"]
    
    def get_train_examples(self, data):
        """Creates the examples for the given data."""
        examples = []
        
        for (i, line) in enumerate(data.values.tolist()):
            
            guid = line[0]
            text_a = line[1]
            text_b = line[2]
            label = line[-1]
            
            examples.append(InputExample(guid=guid, text_a=text_a, text_b=text_b, label=label))
        
        return examples

    def get_dev_examples(self, data):
        """Creates the examples for the given data."""
        examples = []
        
        for (i, line) in enumerate(data.values.tolist()):
            
            guid = line[0]
            text_a = line[1]
            text_b = line[2]
            label = line[-1]
            
            examples.append(InputExample(guid=guid, text_a=text_a, text_b=text_b, label=label))
        
        return examples

### Converting examples into input features

In [11]:
def convert_examples_to_features(examples, label_list, max_seq_length, tokenizer, output_mode):
    
    features = []

    for (ex_index, example) in enumerate(examples):
        if ex_index % 100000 == 0:
            print("writing example %d of %d" % (ex_index, len(examples)))
        
        tokens_a = tokenizer.tokenize(example.text_a)
        tokens_b = tokenizer.tokenize(example.text_b)

        # Modify the tokens_a and tokens_b in place, so that the total length is less than the specified length.
        # account for [CLS], [SEP], [SEP] tokens
        _truncate_seq_pair(tokens_a, tokens_b, max_seq_length - 3)

        # convert the tokens into BERT format
        # add the CLS and SEP tokens to the first sequence a
        tokens = ["[CLS]"] + tokens_a + ["[SEP]"]
        # for the first sequence a, segment ids are 0
        segment_ids = [0] * len(tokens)
        
        # add the SEP token at the end of sequence b
        tokens += tokens_b + ["[SEP]"]
        # for the second sequence b, segmenet ids are 1
        segment_ids += [1] * (len(tokens_b) + 1)
        
        input_ids = tokenizer.convert_tokens_to_ids(tokens)
        
        # The mask has 1 for real tokens and 0 for padding tokens.
        # Only real tokens are attended to.
        input_mask = [1] * len(input_ids)
        
        # Zero-padding upto max_seq_length
        padding = [0] * (max_seq_length - len(input_ids))
        input_ids += padding
        input_mask += padding
        segment_ids += padding
        
        assert len(input_ids) == max_seq_length
        assert len(input_mask) == max_seq_length
        assert len(segment_ids) == max_seq_length
        
        label_id = example.label
       
        features.append(
            InputFeatures(
                input_ids=input_ids,
                input_mask=input_mask,
                segment_ids=segment_ids,
                label_id=label_id))

    return features

In [12]:
def _truncate_seq_pair(tokens_a, tokens_b, max_length):
    """Truncates a sequence pair in place to the maximum length."""
    
    # This is a simple heuristic which will always truncate the longer sequence
    # one token at a time. This makes more sense than truncating an equal percent
    # of tokens from each, since if one sequence is very short then each token
    # that's truncated likely contains more information than a longer sequence.
    
    while True:
        total_length = len(tokens_a) + len(tokens_b)
        if total_length <= max_length:
            break
        if len(tokens_a) > len(tokens_b):
            tokens_a.pop()
        else:
            tokens_b.pop()

### Metrics

Metrics for evaluation (if neccessary)

In [13]:
def simple_accuracy(preds, labels):
    return (preds == labels).mean()

def acc_and_f1(preds, labels):
    acc = simple_accuracy(preds, labels)
    f1 = f1_score(y_true=labels, y_pred=preds)
    
    return {"acc": acc, "f1": f1}

### Model Parameters

In [14]:
output_mode = 'classification'
bert_model = 'bert-base-multilingual-cased'

train_batch_size = 32
gradient_accumulation_steps = 1
num_train_epochs = 3.0

learning_rate = 2e-5
warmup_proportion = 0.1
max_seq_length = 128

eval_batch_size = 8

cache_dir = os.path.join("", "pytorch_pretrained_models")
output_dir = os.path.join("", "out_dir") 

### Initial Setup 

Defining the device 

Setting the random seeds

In [15]:
random.seed(42)
np.random.seed(42)
torch.manual_seed(42)
torch.cuda.manual_seed_all(42)

Creating the output dir, if not present

In [16]:
if not os.path.exists(output_dir):
    os.makedirs(output_dir)

**Creating the Processor and getting the BERT tokenizer**

In [17]:
processor = DataPreProcessor()

label_list = processor.get_labels()
num_labels = len(label_list)

# bert tokenizer
tokenizer = BertTokenizer.from_pretrained(bert_model, do_lower_case=True)

100%|██████████| 995526/995526 [00:00<00:00, 1907803.39B/s]


## Training

Read the train data and convert the training data into examples

In [18]:
train_examples = processor.get_train_examples(train)

In [19]:
num_train_optimization_steps = int(len(train_examples) / train_batch_size / gradient_accumulation_steps) * num_train_epochs
print(num_train_optimization_steps)

42828.0


### Load the pretrained BERT model

In [20]:
model = BertForSequenceClassification.from_pretrained(bert_model, cache_dir=cache_dir, num_labels=num_labels)

100%|██████████| 662804195/662804195 [00:25<00:00, 26393127.44B/s]


Move the model to appropriate device

In [21]:
model.to(device)

BertForSequenceClassification(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(119547, 768)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): BertLayerNorm()
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0): BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): BertLayerNorm()
              (dropout): Dropout(p=0.1, inplace=False)
            )
   

### Training Parameters

Create the Optimizer for training the model

In [22]:
param_optimizer = list(model.named_parameters())
no_decay = ['bias', 'LayerNorm.bias', 'LayerNorm.weight']
optimizer_grouped_parameters = [
    {'params': [p for n, p in param_optimizer if not any(nd in n for nd in no_decay)], 'weight_decay': 0.01},
    {'params': [p for n, p in param_optimizer if any(nd in n for nd in no_decay)], 'weight_decay': 0.0}
]

optimizer = BertAdam(
    optimizer_grouped_parameters,
    lr=learning_rate,
    warmup=warmup_proportion,
    t_total=num_train_optimization_steps
)

In [23]:
global_step = 0
nb_tr_steps = 0
tr_loss = 0

### Training Input

Convert the training examples into training features

In [24]:
train_features = convert_examples_to_features(train_examples, label_list, max_seq_length, tokenizer, output_mode)

writing example 0 of 456857
writing example 100000 of 456857
writing example 200000 of 456857
writing example 300000 of 456857
writing example 400000 of 456857


In [25]:
print("***** Running training *****")
print("  Num examples = %d", len(train_examples))
print("  Batch size = %d", train_batch_size)
print("  Num steps = %d", num_train_optimization_steps)

***** Running training *****
  Num examples = %d 456857
  Batch size = %d 32
  Num steps = %d 42828.0


### Data Loader for Training data

- Wrap the all the training data as a TensorDataset
- Create a RandomSampler for sampling the data
- Create a DataLoader for loading a batch of data


In [26]:
all_input_ids = torch.tensor([f.input_ids for f in train_features], dtype=torch.long)
all_input_mask = torch.tensor([f.input_mask for f in train_features], dtype=torch.long)
all_segment_ids = torch.tensor([f.segment_ids for f in train_features], dtype=torch.long)
all_label_ids = torch.tensor([f.label_id for f in train_features], dtype=torch.long)

train_data = TensorDataset(all_input_ids, all_input_mask, all_segment_ids, all_label_ids)

train_sampler = RandomSampler(train_data)

train_dataloader = DataLoader(train_data, sampler=train_sampler, batch_size=train_batch_size)

### Train the model

-  Load a batch of data
- Get the logits for the batch of data
- Calculate the loss 
- Update the model parameters using Optimizer w.r.t loss


In [27]:
model.train()

weights = torch.tensor([1, 20], dtype=torch.float, device=device)

for _ in trange(int(num_train_epochs), desc='Epoch'):
    tr_loss = 0
    nb_tr_examples, nb_tr_steps = 0, 0
    
    for step, batch in enumerate(tqdm(train_dataloader, desc="Iteration")):
        batch = tuple(t.to(device) for t in batch)
        
        input_ids, input_mask, segment_ids, label_ids = batch
        
        logits = model(input_ids, segment_ids, input_mask, labels=None)

        loss_fct = CrossEntropyLoss(weight=weights)
        loss = loss_fct(logits.view(-1, num_labels), label_ids.view(-1))
        
        optimizer.zero_grad()
        loss.backward()
        
        tr_loss += loss.item()
        nb_tr_examples += input_ids.size(0)
        nb_tr_steps += 1
        
        optimizer.step()
        global_step += 1
        
    print("Training Loss: %s" % (str(tr_loss)))
        
        

Iteration:   0%|          | 0/14277 [00:00<?, ?it/s]/opt/conda/lib/python3.7/site-packages/pytorch_pretrained_bert/optimization.py:132: UserWarning: This overload of add_ is deprecated:
	add_(Number alpha, Tensor other)
Consider using one of the following signatures instead:
	add_(Tensor other, *, Number alpha) (Triggered internally at  /opt/conda/conda-bld/pytorch_1595629427478/work/torch/csrc/utils/python_arg_parser.cpp:766.)
  next_m.mul_(beta1).add_(1 - beta1, grad)

Iteration:   2%|▏         | 234/14277 [02:06<2:04:04,  1.89it/s]


Iteration:   3%|▎         | 474/14277 [04:14<2:02:06,  1.88it/s]


Iteration:   5%|▌         | 714/14277 [06:22<2:01:22,  1.86it/s]


Iteration:   7%|▋         | 954/14277 [08:31<2:01:47,  1.82it/s]


Iteration:   8%|▊         | 1191/14277 [10:37<1:55:50,  1.88it/s]


...

Iteration:  96%|█████████▌| 13658/14277 [2:00:44<05:27,  1.89it/s]


Iteration:  97%|█████████▋| 13892/14277 [2:02:48<03:41,  1.74it/s]


Iteration:  99%|█████████▉| 14126/14277 [2:04:52<01:23,  1.81it/s]


Epoch: 100%|██████████| 3/3 [6:18:57<00:00, 7579.13s/it]  

Training Loss: 319.6606760626091


### Save and Load the trained model

- save the model weights
- save the model config
- Load the model for evaluation


In [28]:
model_to_save = model.module if hasattr(model, 'module') else model
output_model_file = os.path.join(output_dir, WEIGHTS_NAME)
torch.save(model_to_save.state_dict(), output_model_file)

output_config_file = os.path.join(output_dir, CONFIG_NAME)
with open(output_config_file, 'w') as f:
    f.write(model_to_save.config.to_json_string())

config = BertConfig(output_config_file)
model = BertForSequenceClassification(config, num_labels=num_labels)
model.load_state_dict(torch.load(output_model_file))

<All keys matched successfully>

Move the model to appropriate device

In [29]:
model.to(device)

BertForSequenceClassification(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(119547, 768)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): BertLayerNorm()
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0): BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): BertLayerNorm()
              (dropout): Dropout(p=0.1, inplace=False)
            )
   

## Evaluation

Read the evaluation data and convert the evaluation data into examples

Convert the examples into features

In [30]:
# eval_examples = processor.get_dev_examples(eval)
# eval_features = convert_examples_to_features(eval_examples, label_list, max_seq_length, tokenizer, output_mode)

In [31]:
# print("***** Running evaluation *****")
# print("  Num examples = %d", len(eval_examples))
# print("  Batch size = %d", eval_batch_size)

### Data Loader for Evaluation data

- Wrap the all the evaluation data as a TensorDataset
- Create a SequentialSampler for sampling the data
- Create a DataLoader for loading a batch of data

In [32]:
# all_input_ids = torch.tensor([f.input_ids for f in eval_features], dtype=torch.long)
# all_input_mask = torch.tensor([f.input_mask for f in eval_features], dtype=torch.long)
# all_segment_ids = torch.tensor([f.segment_ids for f in eval_features], dtype=torch.long)
# all_label_ids = torch.tensor([f.label_id for f in eval_features], dtype=torch.long)

In [33]:
# eval_data = TensorDataset(all_input_ids, all_input_mask, all_segment_ids, all_label_ids)
# eval_sampler = SequentialSampler(eval_data)
# eval_dataloader = DataLoader(eval_data, sampler=eval_sampler, batch_size=eval_batch_size)

In [34]:
# eval_loss = 0
# nb_eval_steps = 0
# preds = []

### Evaluation and Metrics on Predictions

In [35]:
# model.eval()
# for input_ids, input_mask, segment_ids, label_ids in tqdm(eval_dataloader, desc="Evaluating"):
#     input_ids = input_ids.to(device)
#     input_mask = input_mask.to(device)
#     segment_ids = segment_ids.to(device)
#     label_ids = label_ids.to(device)

#     with torch.no_grad():
#         logits = model(input_ids, segment_ids, input_mask, labels=None)

#     # create eval loss and other metric required by the task
#     loss_fct = CrossEntropyLoss()
#     tmp_eval_loss = loss_fct(logits.view(-1, num_labels), label_ids.view(-1))

#     eval_loss += tmp_eval_loss.mean().item()
#     nb_eval_steps += 1
#     if len(preds) == 0:
#         preds.append(logits.detach().cpu().numpy())
#     else:
#         preds[0] = np.append(
#             preds[0], logits.detach().cpu().numpy(), axis=0)

# eval_loss = eval_loss / nb_eval_steps
# preds = preds[0]
# preds = np.argmax(preds, axis=1)

# result = acc_and_f1(preds, all_label_ids.numpy())
# print(result)

In [36]:
# !ls

In [43]:
test = pd.read_csv('/kaggle/input/sibur-2020-nlp-classification/test_bert.csv')

test.name_1 = test.name_1.str.strip()
test.name_2 = test.name_2.str.strip()

test['is_duplicate'] = 0
test.fillna('', inplace=True)

test.insert(0, 'pair_id', test.index)


test.head()

pair_id                         name_1                            name_2  \
0        0          sun blinds decoration                  indl  cuautitlan   
1        1                            eih           wei shi plastic product   
2        2                            jsh  arab shipbuilding  repair yard c   
3        3              better industrial                farmacap industria   
4        4  equipos inoxidables del norte                               bel   

   is_duplicate  
0             0  
1             0  
2             0  
3             0  
4             0

In [44]:
test.shape

(213249, 4)

In [45]:
test_examples = processor.get_dev_examples(test)
test_features = convert_examples_to_features(test_examples, label_list, max_seq_length, tokenizer, output_mode)

writing example 0 of 213249
writing example 100000 of 213249
writing example 200000 of 213249


In [46]:
all_input_ids = torch.tensor([f.input_ids for f in test_features], dtype=torch.long)
all_input_mask = torch.tensor([f.input_mask for f in test_features], dtype=torch.long)
all_segment_ids = torch.tensor([f.segment_ids for f in test_features], dtype=torch.long)
all_label_ids = torch.tensor([f.label_id for f in test_features], dtype=torch.long)

In [47]:
test_batch_size = 8

test_data = TensorDataset(all_input_ids, all_input_mask, all_segment_ids, all_label_ids)
test_sampler = SequentialSampler(test_data)
test_dataloader = DataLoader(test_data, sampler=test_sampler, batch_size=test_batch_size)

In [48]:
test_loss = 0
nb_test_steps = 0
preds = []

In [49]:
model.eval()
for input_ids, input_mask, segment_ids, label_ids in tqdm(test_dataloader, desc="Predicting"):
    input_ids = input_ids.to(device)
    input_mask = input_mask.to(device)
    segment_ids = segment_ids.to(device)
    label_ids = label_ids.to(device)

    with torch.no_grad():
        logits = model(input_ids, segment_ids, input_mask, labels=None)

    # create eval loss and other metric required by the task
    loss_fct = CrossEntropyLoss()
    tmp_test_loss = loss_fct(logits.view(-1, num_labels), label_ids.view(-1))

    test_loss += tmp_test_loss.mean().item()
    nb_test_steps += 1
    if len(preds) == 0:
        preds.append(logits.detach().cpu().numpy())
    else:
        preds[0] = np.append(
            preds[0], logits.detach().cpu().numpy(), axis=0)

test_loss = test_loss / nb_test_steps
preds = preds[0]
preds = np.argmax(preds, axis=1)

print(preds.shape)

print(preds)

Predicting: 100%|██████████| 26657/26657 [18:00<00:00, 24.68it/s]

(213249,)
[0 0 0 ... 0 0 0]


In [55]:
preds.shape

(213249,)

In [50]:
type(preds)

numpy.ndarray

In [56]:
test['is_duplicate'] = preds

In [57]:
test.is_duplicate.value_counts()

0    212606
1       643
Name: is_duplicate, dtype: int64

In [68]:
pd.RangeIndex(start=1, stop=213250, step=1)

RangeIndex(start=1, stop=213249, step=1)

In [69]:
test['pair_id'] = pd.RangeIndex(start=1, stop=213250, step=1)

In [70]:
test

pair_id                         name_1  \
0             1          sun blinds decoration   
1             2                            eih   
2             3                            jsh   
3             4              better industrial   
4             5  equipos inoxidables del norte   
...         ...                            ...   
213244   213245                 dyna logistics   
213245   213246                            dsi   
213246   213247         saint gobain abrasives   
213247   213248                       covestro   
213248   213249                         zandur   

                                            name_2  is_duplicate  
0                                 indl  cuautitlan             0  
1                          wei shi plastic product             0  
2                 arab shipbuilding  repair yard c             0  
3                               farmacap industria             0  
4                                              bel             0  
...                                            ...           ...  
213244                    jiangsu easero logistics             0  
213245                          kavalani  sons wll             0  
213246                                      zarabi             0  
213247                                   terabytes             0  
213248  qingyuan xierong plastics  rubber products             0  

[213249 rows x 4 columns]

In [71]:
test[['pair_id', 'is_duplicate']].to_csv('submission.csv', index=None)

In [72]:
x = pd.read_csv('/kaggle/working/submission.csv')
x

pair_id  is_duplicate
0             1             0
1             2             0
2             3             0
3             4             0
4             5             0
...         ...           ...
213244   213245             0
213245   213246             0
213246   213247             0
213247   213248             0
213248   213249             0

[213249 rows x 2 columns]

In [73]:
x.is_duplicate.value_counts()

0    212606
1       643
Name: is_duplicate, dtype: int64